In [1]:
import os
# 获取当前文件所在目录
current_dir = os.path.dirname(os.path.abspath(''))
print("当前工作目录:", current_dir)
# 设置工作目录
os.chdir('/data/zlhu/NeuroAI/Eye-of-Brain/Brain-Diffusion/decoding_sd2')
# 验证工作目录
print("当前工作目录:", os.getcwd())

当前工作目录: /data
当前工作目录: /data/zlhu/NeuroAI/Eye-of-Brain/Brain-Diffusion/decoding_sd2


In [4]:
import sys
# 添加Stable Diffusion代码路径
# sys.path.append('./stablediffusion')
# 或使用绝对路径
sys.path.append('/data/zlhu/NeuroAI/Eye-of-Brain/Brain-Diffusion/decoding_sd2/stablediffusion')

# 然后再导入模块
from stablediffusion.ldm.data.util import AddMiDaS

In [5]:
import h5py
import scipy.io
from nsd_access.nsda import NSDAccess

In [6]:
import argparse, os
from tqdm import tqdm, trange
from torch import autocast
from contextlib import nullcontext
import torch
import numpy as np
import pandas as pd
from PIL import Image
import PIL
from omegaconf import OmegaConf
from einops import repeat, rearrange
from pytorch_lightning import seed_everything
from ldm.util import instantiate_from_config
from ldm.models.diffusion.ddim import DDIMSampler
from stablediffusion.ldm.data.util import AddMiDaS

In [7]:
def initialize_model(config, ckpt,device):
    config = OmegaConf.load(config)
    model = instantiate_from_config(config.model)
    model.load_state_dict(torch.load(ckpt)["state_dict"], strict=False)
    model = model.to(device)
    sampler = DDIMSampler(model)
    return sampler

In [8]:
def pad_image(input_image):
    pad_w, pad_h = np.max(((2, 2), np.ceil(
        np.array(input_image.size) / 64).astype(int)), axis=0) * 64 - input_image.size
    im_padded = Image.fromarray(
        np.pad(np.array(input_image), ((0, pad_h), (0, pad_w), (0, 0)), mode='edge'))
    return im_padded

In [9]:
def make_batch_sd(
        image,
        txt,
        device,
        num_samples=1,
        model_type="dpt_hybrid"
):
    image = np.array(image.convert("RGB"))
    image = torch.from_numpy(image).to(dtype=torch.float32) / 127.5 - 1.0
    # sample['jpg'] is tensor hwc in [-1, 1] at this point
    midas_trafo = AddMiDaS(model_type=model_type)
    batch = {
        "jpg": image,
        "txt": txt,
    }
    batch = midas_trafo(batch)
    batch["jpg"] = rearrange(batch["jpg"], 'h w c -> 1 c h w')
    batch["jpg"] = repeat(batch["jpg"].to(device=device),
                          "1 ... -> n ...", n=num_samples)
    batch["midas_in"] = repeat(torch.from_numpy(batch["midas_in"][None, ...]).to(
        device=device), "1 ... -> n ...", n=num_samples)
    return batch

In [10]:
def load_img_from_arr(img_arr):
    image = Image.fromarray(img_arr).convert("RGB")
    w, h = 512, 512
    image = image.resize((w, h), resample=PIL.Image.LANCZOS)
    image = np.array(image).astype(np.float32) / 255.0
    image = image[None].transpose(0, 3, 1, 2)
    image = torch.from_numpy(image)
    return 2.*image - 1.

In [11]:
# parser = argparse.ArgumentParser()

# parser.add_argument(
#     "--imgidxs",
#     required=True,
#     nargs="*",
#     type=int,
#     help="start and end imgs"
# )
# parser.add_argument(
#     "--gpu",
#     required=True,
#     type=int,
#     help="gpu"
# )
# parser.add_argument(
#     "--seed",
#     type=int,
#     default=42,
#     help="the seed (for reproducible sampling)",
# )
# parser.add_argument(
#     "--subject",
#     required=True,
#     type=str,
#     default=None,
#     help="subject name: subj01 or subj02  or subj05  or subj07 for full-data subjects ",
# )

# Set parameters
# opt = parser.parse_args()
# seed_everything(opt.seed)
# imgidxs = opt.imgidxs
# gpu = opt.gpu
# subject=opt.subject

In [12]:
# Set parameters
seed = 42
imgidx = 0
# imgidxs = 
gpu = 0
subject = 'subj01'

In [13]:

# Load NSD information
nsd_expdesign = scipy.io.loadmat('../../data/nsd/nsddata/experiments/nsd/nsd_expdesign.mat')

nsda = NSDAccess('../../data/nsd/')
sf = h5py.File(nsda.stimuli_file, 'r')
sdataset = sf.get('imgBrick')

stims_ave = np.load(f'../../data/stim/{subject}/{subject}_stims_ave.npy')

# Note that mos of them are 1-base index!
# This is why I subtract 1
sharedix = nsd_expdesign['sharedix'] -1 
tr_idx = np.zeros_like(stims_ave)
for idx, s in enumerate(stims_ave):
    if s in sharedix:
        tr_idx[idx] = 0
    else:
        tr_idx[idx] = 1

In [14]:
print(torch.cuda.is_available())
print(torch.cuda.device_count())

True
1


In [15]:
torch.cuda.set_device(gpu)
config = './stablediffusion/configs/stable-diffusion/v2-midas-inference.yaml'
ckpt = './stablediffusion/models/512-depth-ema.ckpt'
steps = 50
scale = 5.0
eta = 0.0
strength = 0.8
num_samples= 1
callback=None
n_iter = 5

In [16]:
# Save Directories
outdir = f'../../Brain-Decoded/{subject}/image-text-depth'
os.makedirs(outdir, exist_ok=True)
sample_path = os.path.join(outdir, f"samples")
os.makedirs(sample_path, exist_ok=True)

In [21]:
precision = 'autocast'
precision_scope = autocast if precision == "autocast" else nullcontext

In [22]:
device = torch.device(f"cuda:{gpu}") if torch.cuda.is_available() else torch.device("cpu")
sampler = initialize_model(config, ckpt,device)
model = sampler.model

TypeError: Unexpected file type

In [17]:
def load_model_from_config(config, ckpt, gpu, verbose=False):
    print(f"Loading model from {ckpt}")
    pl_sd = torch.load(ckpt, map_location="cpu")
    if "global_step" in pl_sd:
        print(f"Global Step: {pl_sd['global_step']}")
    sd = pl_sd["state_dict"]
    model = instantiate_from_config(config.model)
    m, u = model.load_state_dict(sd, strict=False)
    if len(m) > 0 and verbose:
        print("missing keys:")
        print(m)
    if len(u) > 0 and verbose:
        print("unexpected keys:")
        print(u)
    model.cuda(f"cuda:{gpu}")
    model.eval()
    return model

In [20]:
torch.cuda.set_device(gpu)
model = initialize_model(config, ckpt, gpu)

Loading model from ./stablediffusion/models/512-depth-ema.ckpt


/tmp/ipykernel_20493/215837999.py:3: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  pl_sd = torch.load(ckpt, map_location="cpu")


Global Step: 190000


AttributeError: module 'ldm.models.diffusion.ddpm' has no attribute 'LatentDepth2ImageDiffusion'

In [18]:
precision = 'autocast'
device = torch.device(f"cuda:{gpu}") if torch.cuda.is_available() else torch.device("cpu")
model = model.to(device)
sampler = DDIMSampler(model)

sampler.make_schedule(ddim_num_steps=steps, ddim_eta=eta, verbose=False)

assert 0. <= strength <= 1., 'can only work with strength in [0.0, 1.0]'
t_enc = int(strength * steps)
print(f"target t_enc is {t_enc} steps")

NameError: name 'model' is not defined

In [13]:
precision = 'autocast'
precision_scope = autocast if precision == "autocast" else nullcontext


device = torch.device(f"cuda:{gpu}") if torch.cuda.is_available() else torch.device("cpu")
sampler = initialize_model(config, ckpt,device)
model = sampler.model

# 调度策略
sampler.make_schedule(ddim_num_steps=steps, ddim_eta=eta, verbose=True)

assert 0. <= strength <= 1., 'can only work with strength in [0.0, 1.0]'

t_enc = min(int(strength * steps), steps-1)
print(f"target t_enc is {t_enc} steps")

AttributeError: module 'ldm.models.diffusion.ddpm' has no attribute 'LatentDepth2ImageDiffusion'

In [15]:
# Load Prediction (C, InitLatent, Depth(cc))
captdir = f'../data/decoded/{subject}/captions/'
dptdir = f'../data/decoded/{subject}/dpt_fromemb/'
gandir = f'../data/decoded/gan_recon_img/all_layers/{subject}/streams/'

# C
captions = pd.read_csv(f'{captdir}/captions_brain.csv', sep='\t',header=None)

In [ ]:
### decoding NO.1 第一版

# Save Directories
outdir = f'../../decoded/image-depth/{subject}/'
os.makedirs(outdir, exist_ok=True)
sample_path = os.path.join(outdir, f"samples")
os.makedirs(sample_path, exist_ok=True)

# padding-batch
for imgidx in range(982):
    
    print(f"now is img{imgidx}.../n")
    # Load z (Image)
    imgidx_te = np.where(tr_idx==0)[0][imgidx] # Extract test image index
    idx73k= stims_ave[imgidx_te]
    Image.fromarray(np.squeeze(sdataset[idx73k,:,:,:]).astype(np.uint8)).save(
        os.path.join(sample_path, f"{imgidx:05}_org.png"))
    
    # get caption and depth
    prompt = [captions.iloc[imgidx][0]]
    cc = torch.Tensor(np.load(f'{dptdir}/{imgidx:06}.npy')).to('cuda')
    
    # # Generate image from Text + GAN + Depth
    # shenpath = f'{gandir}/recon_image_normalized-VGG19-fc8-{subject}-streams-{imgidx:06}.tiff'
    # init_image = Image.open(shenpath).resize((512,512))
    
    # Generate image from Text + Depth
    
    roi_latent = 'early'
    scores_latent = np.load(f'../../decoded/{subject}/{subject}_{roi_latent}_scores_init_latent.npy')
    imgarr = torch.Tensor(scores_latent[imgidx,:].reshape(4,40,40)).unsqueeze(0).to('cuda')
    
    # Generate image from Z
    precision_scope = autocast if precision == "autocast" else nullcontext
    with torch.no_grad():
        with precision_scope("cuda"):
            with model.ema_scope():
                x_samples = model.decode_first_stage(imgarr)
                x_samples = torch.clamp((x_samples + 1.0) / 2.0, min=0.0, max=1.0)
    
                for x_sample in x_samples:
                    x_sample = 255. * rearrange(x_sample.cpu().numpy(), 'c h w -> h w c')
    init_image = Image.fromarray(x_sample.astype(np.uint8)).resize((512,512))
    image = pad_image(init_image)
    
    base_count = 0
    with torch.no_grad():
        for n in trange(n_iter, desc="Sampling"):
            torch.autocast("cuda")
            batch = make_batch_sd(image, txt=prompt, device=device, num_samples=num_samples)
            z = model.get_first_stage_encoding(model.encode_first_stage(
                batch[model.first_stage_key]))  # move to latent space
            c = model.cond_stage_model.encode(batch["txt"]).mean(axis=0).unsqueeze(0)
            c_cat = list()
            c_cat.append(cc)
            c_cat = torch.cat(c_cat, dim=1)
    
            # cond
            cond = {"c_concat": [c_cat], "c_crossattn": [c]}
    
            # uncond cond
            uc_cross = model.get_unconditional_conditioning(num_samples, "")
            uc_full = {"c_concat": [c_cat], "c_crossattn": [uc_cross]}
    
            # encode (scaled latent)
            z_enc = sampler.stochastic_encode(
                z, torch.tensor([t_enc] * num_samples).to(model.device))
    
            # decode it
            samples = sampler.decode(z_enc, cond, t_enc, unconditional_guidance_scale=scale,
                                    unconditional_conditioning=uc_full, callback=callback)
            x_samples_ddim = model.decode_first_stage(samples)
            result = torch.clamp((x_samples_ddim + 1.0) / 2.0, min=0.0, max=1.0)
            result = result.cpu().numpy().transpose(0, 2, 3, 1) * 255
            Image.fromarray(result[0,:,:,:].astype(np.uint8)).save(
                os.path.join(sample_path, f"{imgidx:05}_{base_count:03}.png"))   
            base_count += 1

now is img0.../n


Sampling:   0%|                                                        | 0/5 [00:00<?, ?it/s]

Running DDIM Sampling with 40 timesteps



Sampling:  20%|█████████▌                                      | 1/5 [00:12<00:48, 12.22s/it]

Running DDIM Sampling with 40 timesteps


...


Sampling:  40%|███████████████████▏                            | 2/5 [00:25<00:37, 12.56s/it]

Running DDIM Sampling with 40 timesteps



Sampling:  60%|████████████████████████████▊                   | 3/5 [00:37<00:25, 12.56s/it]

Running DDIM Sampling with 40 timesteps



Decoding image:  80%|████████████████████████████████        | 32/40 [00:09<00:02,  3.30it/s]

In [12]:
### decoding NO.2 第二版

# Save Directories
outdir = f'../../decoded/image-depth-new2/{subject}/'
os.makedirs(outdir, exist_ok=True)
sample_path = os.path.join(outdir, f"samples")
os.makedirs(sample_path, exist_ok=True)

for imgidx in range(101):

    c = model.get_learned_conditioning(captions.iloc[imgidx][0]).to('cuda')
    cc = torch.Tensor(np.load(f'{dptdir}/{imgidx:06}.npy')).to('cuda')
    
    # # Generate image from Text + GAN + Depth
    # shenpath = f'{gandir}/recon_image_normalized-VGG19-fc8-{subject}-streams-{imgidx:06}.tiff'
    # init_image = Image.open(shenpath).resize((512,512))
    
    # Generate image from Text + Depth
    
    roi_latent = 'early'
    scores_latent = np.load(f'../../decoded/{subject}/{subject}_{roi_latent}_scores_init_latent.npy')
    imgarr = torch.Tensor(scores_latent[imgidx,:].reshape(4,40,40)).unsqueeze(0).to('cuda')
    
    # Generate image from Z
    precision_scope = autocast if precision == "autocast" else nullcontext
    with torch.no_grad():
        with precision_scope("cuda"):
            with model.ema_scope():
                x_samples = model.decode_first_stage(imgarr)
                x_samples = torch.clamp((x_samples + 1.0) / 2.0, min=0.0, max=1.0)
    
                for x_sample in x_samples:
                    x_sample = 255. * rearrange(x_sample.cpu().numpy(), 'c h w -> h w c')
    
    im = Image.fromarray(x_sample.astype(np.uint8)).resize((512,512))
    im = np.array(im)
    init_image = load_img_from_arr(im).to('cuda')
    init_latent = model.get_first_stage_encoding(model.encode_first_stage(init_image))  # move to latent space
    
    base_count = 0
    with torch.no_grad():
        for n in trange(n_iter, desc="Sampling"):
            torch.autocast("cuda")
            
            c_cat = list()
            c_cat.append(cc)
            c_cat = torch.cat(c_cat, dim=1)
    
            # cond
            cond = {"c_concat": [c_cat], "c_crossattn": [c]}
    
            # uncond cond
            uc_cross = model.get_unconditional_conditioning(num_samples, "")
            uc_full = {"c_concat": [c_cat], "c_crossattn": [uc_cross]}
    
            # encode (scaled latent)
            z_enc = sampler.stochastic_encode(
                init_latent, torch.tensor([t_enc] * num_samples).to(model.device))
    
            # decode it
            samples = sampler.decode(z_enc, cond, t_enc, unconditional_guidance_scale=scale,
                                    unconditional_conditioning=uc_full, callback=callback)
            x_samples_ddim = model.decode_first_stage(samples)
            result = torch.clamp((x_samples_ddim + 1.0) / 2.0, min=0.0, max=1.0)
            result = result.cpu().numpy().transpose(0, 2, 3, 1) * 255
            Image.fromarray(result[0,:,:,:].astype(np.uint8)).save(
                os.path.join(sample_path, f"{imgidx:05}_{base_count:03}.png"))   
            base_count += 1

Sampling:   0%|                                                        | 0/5 [00:00<?, ?it/s]

Running DDIM Sampling with 40 timesteps



Sampling:  20%|█████████▌                                      | 1/5 [00:12<00:48, 12.11s/it]

Running DDIM Sampling with 40 timesteps



Sampling:  40%|███████████████████▏                            | 2/5 [00:24<00:36, 12.15s/it]

...


Sampling:  60%|████████████████████████████▊                   | 3/5 [00:37<00:24, 12.39s/it]

Running DDIM Sampling with 40 timesteps



Sampling:  80%|██████████████████████████████████████▍         | 4/5 [00:49<00:12, 12.38s/it]

Running DDIM Sampling with 40 timesteps



Sampling: 100%|████████████████████████████████████████████████| 5/5 [01:01<00:00, 12.40s/it]


In [15]:
### decoding NO.3 第三版

# Save Directories
outdir = f'../../decoded/image-depth-new3/{subject}/'
os.makedirs(outdir, exist_ok=True)
sample_path = os.path.join(outdir, f"samples")
os.makedirs(sample_path, exist_ok=True)

for imgidx in range(101):
    prompt = [captions.iloc[imgidx][0]]
    cc = torch.Tensor(np.load(f'{dptdir}/{imgidx:06}.npy')).to('cuda')
    
    # # Generate image from Text + GAN + Depth
    # shenpath = f'{gandir}/recon_image_normalized-VGG19-fc8-{subject}-streams-{imgidx:06}.tiff'
    # init_image = Image.open(shenpath).resize((512,512))
    
    # Generate image from Text + Depth
    
    roi_latent = 'early'
    scores_latent = np.load(f'../../decoded/{subject}/{subject}_{roi_latent}_scores_init_latent.npy')
    imgarr = torch.Tensor(scores_latent[imgidx,:].reshape(4,40,40)).unsqueeze(0).to('cuda')
    
    # Generate image from Z
    precision_scope = autocast if precision == "autocast" else nullcontext
    with torch.no_grad():
        with precision_scope("cuda"):
            with model.ema_scope():
                x_samples = model.decode_first_stage(imgarr)
                x_samples = torch.clamp((x_samples + 1.0) / 2.0, min=0.0, max=1.0)
    
                for x_sample in x_samples:
                    x_sample = 255. * rearrange(x_sample.cpu().numpy(), 'c h w -> h w c')
    image = Image.fromarray(x_sample.astype(np.uint8)).resize((512,512))
    # image = pad_image(init_image)
    
    base_count = 0
    with torch.no_grad():
        for n in trange(n_iter, desc="Sampling"):
            torch.autocast("cuda")
            batch = make_batch_sd(image, txt=prompt, device=device, num_samples=num_samples)
            z = model.get_first_stage_encoding(model.encode_first_stage(
                batch[model.first_stage_key]))  # move to latent space
            c = model.cond_stage_model.encode(batch["txt"]).mean(axis=0).unsqueeze(0)
            c_cat = list()
            c_cat.append(cc)
            c_cat = torch.cat(c_cat, dim=1)
    
            # cond
            cond = {"c_concat": [c_cat], "c_crossattn": [c]}
    
            # uncond cond
            uc_cross = model.get_unconditional_conditioning(num_samples, "")
            uc_full = {"c_concat": [c_cat], "c_crossattn": [uc_cross]}
    
            # encode (scaled latent)
            z_enc = sampler.stochastic_encode(
                z, torch.tensor([t_enc] * num_samples).to(model.device))
    
            # decode it
            samples = sampler.decode(z_enc, cond, t_enc, unconditional_guidance_scale=scale,
                                    unconditional_conditioning=uc_full, callback=callback)
            x_samples_ddim = model.decode_first_stage(samples)
            result = torch.clamp((x_samples_ddim + 1.0) / 2.0, min=0.0, max=1.0)
            result = result.cpu().numpy().transpose(0, 2, 3, 1) * 255
            Image.fromarray(result[0,:,:,:].astype(np.uint8)).save(
                os.path.join(sample_path, f"{imgidx:05}_{base_count:03}.png"))   
            base_count += 1

Sampling:   0%|                                                        | 0/5 [00:00<?, ?it/s]

Running DDIM Sampling with 40 timesteps



Sampling:  20%|█████████▌                                      | 1/5 [00:11<00:47, 11.94s/it]

Running DDIM Sampling with 40 timesteps



Sampling:  40%|███████████████████▏                            | 2/5 [00:23<00:35, 11.98s/it]

...


Sampling:  80%|██████████████████████████████████████▍         | 4/5 [00:48<00:12, 12.23s/it]

Running DDIM Sampling with 40 timesteps



Sampling:   0%|                                                        | 0/5 [00:00<?, ?it/s]

Running DDIM Sampling with 40 timesteps



Decoding image:   2%|█                                        | 1/40 [00:00<00:11,  3.45it/s]IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [ ]:
### decoding NO.4 第四版
# Save Directories
outdir = f'../../decoded/image-depth-new4/{subject}/'
os.makedirs(outdir, exist_ok=True)
sample_path = os.path.join(outdir, f"samples")
os.makedirs(sample_path, exist_ok=True)

for imgidx in range(101):
    prompt = [captions.iloc[imgidx][0]]
    cc = torch.Tensor(np.load(f'{dptdir}/{imgidx:06}.npy')).to('cuda')
    
    # # Generate image from Text + GAN + Depth
    # shenpath = f'{gandir}/recon_image_normalized-VGG19-fc8-{subject}-streams-{imgidx:06}.tiff'
    # init_image = Image.open(shenpath).resize((512,512))
    
    # Generate image from Text + Depth
    
    roi_latent = 'early'
    scores_latent = np.load(f'../../decoded/{subject}/{subject}_{roi_latent}_scores_init_latent.npy')
    imgarr = torch.Tensor(scores_latent[imgidx,:].reshape(4,40,40)).unsqueeze(0).to('cuda')
    
    # Generate image from Z
    precision_scope = autocast if precision == "autocast" else nullcontext
    with torch.no_grad():
        with precision_scope("cuda"):
            with model.ema_scope():
                x_samples = model.decode_first_stage(imgarr)
                x_samples = torch.clamp((x_samples + 1.0) / 2.0, min=0.0, max=1.0)
    
                for x_sample in x_samples:
                    x_sample = 255. * rearrange(x_sample.cpu().numpy(), 'c h w -> h w c')
    image = Image.fromarray(x_sample.astype(np.uint8)).resize((512,512))
    im = np.array(im)
    init_image = load_img_from_arr(im).to('cuda')
    init_latent = model.get_first_stage_encoding(model.encode_first_stage(init_image))  # move to latent space
    
    # image = pad_image(init_image)
    
    base_count = 0
    with torch.no_grad():
        for n in trange(n_iter, desc="Sampling"):
            torch.autocast("cuda")
            batch = make_batch_sd(image, txt=prompt, device=device, num_samples=num_samples)
            z = model.get_first_stage_encoding(model.encode_first_stage(
                init_image))  # move to latent space
            c = model.cond_stage_model.encode(batch["txt"]).mean(axis=0).unsqueeze(0)
            c_cat = list()
            c_cat.append(cc)
            c_cat = torch.cat(c_cat, dim=1)
    
            # cond
            cond = {"c_concat": [c_cat], "c_crossattn": [c]}
    
            # uncond cond
            uc_cross = model.get_unconditional_conditioning(num_samples, "")
            uc_full = {"c_concat": [c_cat], "c_crossattn": [uc_cross]}
    
            # encode (scaled latent)
            z_enc = sampler.stochastic_encode(
                z, torch.tensor([t_enc] * num_samples).to(model.device))
    
            # decode it
            samples = sampler.decode(z_enc, cond, t_enc, unconditional_guidance_scale=scale,
                                    unconditional_conditioning=uc_full, callback=callback)
            x_samples_ddim = model.decode_first_stage(samples)
            result = torch.clamp((x_samples_ddim + 1.0) / 2.0, min=0.0, max=1.0)
            result = result.cpu().numpy().transpose(0, 2, 3, 1) * 255
            Image.fromarray(result[0,:,:,:].astype(np.uint8)).save(
                os.path.join(sample_path, f"{imgidx:05}_{base_count:03}.png"))   
            base_count += 1